In [1]:
## Latest Version - Update December 2, 2022
## Compatible with Seeq Versions R58+

## INSTALLATION INSTRUCTIONS ##
## ------------------------- ##
# Before Starting : Open up a duplicate copy of this notebook and click the AppMode button to run it in AppMode.  Copy the Appmode URL, as it will be required in Step 3.
# 2. Click Cell -> Run All in this notebook.  Then scroll to the bottom of this worksheet to the GUI. 
# 3. Using the GUI tools dropdown at the bottom of this notebook, locate any previously installed Add-on Tool Management apps and click uninstall.
# 4. Fill in all of the fields in the GUI, using the URL Target from Step 1.  Then click install.  
#    Suggested settings :
#        Name : Add On Tool Management
#        Description : Add or Modify Add On Tools
#        Icon : fa fa-wrench
#        Link-Type : Window
#        Window Details : toolbar=0,location=0,scrollbars=0,statusbar=0,menubar=0,resizable=0,height=550,width=420
# 5. Within this notebook click Cell -> All Output -> Clear.  Then save this notebook.  It can now be closed.
# 6. Return to workbench, REFRESH the page, and confirm the updated Add-on Tool Management UI is available.  The tool
#    can be used to tweak the height and width of the window if required using the 'modify' button.

In [2]:
from IPython.display import display, HTML, clear_output
import ipyvuetify as vue
import ipywidgets as ipw
import functools
import time
from seeq import sdk
import itertools

users_api = sdk.UsersApi(spy.client)

In [3]:
%%html
<style>
    div#notebook { padding-top:0px !important; }
    div#notebook { padding-bottom: 0px !important}
    .container { width:100% !important; }
    .end_space { min-height:0px !important; }
    div.output_subarea.jupyter-widgets-view { max-width: 100%}
    .widget-radio-box { flex-direction: row !important;}
    .widget-radio-box label{margin:5px;}
    .widget-radio-box {margin-bottom:0px !important;}
    .p-Widget jupyter-widgets widget-label {margin-left: 75px !important;}
    .end_space {line-height: 25px !important;}
</style>

In [4]:
## Utility functions ##

def widget_to_dict():
    _dict = {
            "Name": _name.value,
            "Description": _desc.value,
            "Icon": _icon.value,
            "Target URL": _url.value,
            "Link Type": _linkType.value,
            "Window Details": _windowDetails.value,
            "Sort Key": _sortKey.value,
            "Reuse Window": str(_reuseWindow.value).lower() == 'true',
            "Groups": [x.strip() for x in _groupPermissions.value.split(',')] if _groupPermissions.value else '',
            "Users": [x.strip() for x in _userPermissions.value.split(',')] if _userPermissions.value else '',
    }
    
    return {k: v for k, v in _dict.items() if v}

def update_icon(b):
    _icon_out.value = f'<i class="{_icon.value} fa-2x"></i>'

In [5]:
# Main Form UI

modify_section = ipw.Output()

# form fields...
_h_spacer = ipw.HTML(value="", layout=ipw.Layout(width='140px'))
_style = {'description_width': '125px'}

_name = ipw.Text(description='Name',value='New Tool Name', style=_style)
_desc = ipw.Text(description='Description',value='New Tool Description', style=_style)
_icon = ipw.Text(description='Icon',value='fa fa-magic', style=_style)
_url = ipw.Text(description='Target',value='http://www.seeq.com', style=_style)
_linkType = ipw.RadioButtons(description='Link Type',options=['window','tab'], style=_style)
_icon_out = ipw.HTML(value=f'<i class="{_icon.value} fa-2x"></i>', style=_style)

_windowDetails = ipw.Textarea(description='Window Details',
                          value='toolbar=0,location=0,scrollbars=0,statusbar=0,menubar=0,resizable=1,height=600,width=450', 
                          style=_style)

_sortKey = ipw.Text(description='Sort Key',value='z', style=_style)
_reuseWindow = ipw.Checkbox(value=True, disabled=False, indent=False, layout=ipw.Layout(width='auto'))
_groupPermissions = ipw.Text(description='Allowed Groups',value='', style=_style)
_userPermissions = ipw.Text(description='Allowed Users',value=spy.user.email, style=_style)

_box = ipw.VBox([_name,
                 _desc,
                 ipw.HBox([_icon,_icon_out]),
                 _url,
                 _linkType,
                 _windowDetails,
                 _sortKey,
                 ipw.HBox([ipw.Label(value='Reuse Window', layout = ipw.Layout(display='flex', width = '120px', margin= '0 12px 0 0', justify_content='flex-end')), _reuseWindow]),                 
                 _groupPermissions,
                 _userPermissions
                ])

with modify_section:
    display(_box)
    

In [21]:
class UserInterface:
    
    snackbar = vue.Snackbar(v_model=None, top=True, right=True)
    
    def __init__(self):
        self.initialize_ui_components()
    
    def run(self):
        display(self.admin_ui if spy.user.is_admin else self.non_admin_ui)

    def update_form(self, _):
        if self.tools_dropdown.value is None:
            return

        search_result = spy.addons.search(query = {"ID": self.tools_dropdown.value}, quiet=True)

        _name.value = search_result['Name'][0]
        _desc.value = search_result['Description'][0]
        _url.value = search_result['Target URL'][0]
        _icon.value = search_result['Icon'][0]
        _linkType.value = search_result['Link Type'][0]
        _sortKey.value = search_result['Sort Key'][0]
        _reuseWindow.value =  bool(search_result['Reuse Window'][0])
        _windowDetails.value = search_result['Window Details'][0]
        
        user_permissions = list(set([self.get_email_from_username(x) for x in search_result['Users'][0] if self.get_email_from_username(x) is not None]))
        _userPermissions.value = (', ').join(user_permissions)
        _groupPermissions.value = (', ').join(search_result['Groups'][0])
        
    def initialize_ui_components(self):
        # tools dropdown...
        self.tools_dropdown = ipw.Dropdown(description="Tools", style = _style, layout=ipw.Layout(margin= '0 0 0 8px'))
        self.tools_dropdown.observe(self.update_form, names='value')

        # error output
        self.error = ipw.Output()

        # buttons
        self.install_button = ipw.Button(description="Install", button_style='success',layout=ipw.Layout(width='80px'))
        self.modify_button = ipw.Button(description="Modify", button_style='success',layout=ipw.Layout(width='80px'))
        self.clear_button = ipw.Button(description="Reset", button_style='success',layout=ipw.Layout(width='80px'))
        self.uninstall_button = ipw.Button(description="Uninstall", button_style='success',layout=ipw.Layout(width='80px'))
        
        self.install_button.on_click(self.install_tool)
        self.modify_button.on_click(self.modify_tool)
        self.uninstall_button.on_click(self.uninstall_tool)
        self.clear_button.on_click(self.update_form)
        
        # intialize dropdown
        self.update_tool_dropdown()
        
    def get_email_from_username(self, guid):
        email_search = sdk.UsersApi(spy.client).autocomplete_users_and_groups(query = guid).items
        if email_search == []:
            self.snackbar.children = [f'Could not locate user {guid}']
            self.snackbar.color = 'error'
            self.snackbar.v_model = True
            return
        else:
            return email_search[0].email

    def get_username_from_email(self, email):
        email = email.strip().lower()
        users = [user for user in sdk.UsersApi(spy.client).get_users(email_search = email).users if user.email.strip().lower()==email]
        if users == []:
            self.snackbar.children = [f'Could not locate user for email {email}.']
            self.snackbar.color = 'error'
            self.snackbar.v_model = True
            return users
        else:
            return [user.username for user in users]
        
    
    @property
    def non_admin_ui(self):
        _sysadmin = sdk.SystemApi(spy.client).get_administrator_contact_information()
        _nonadmin = ipw.HTML(value=f"<center><span style='color:red;font-size:20px'>Only Admins can Modify or Create Tools.<br>Please contact<br><a href = 'mailto: {_sysadmin.name}'>{_sysadmin.name}</a></span><center>")
        return _nonadmin
    
    @property
    def admin_ui(self):
        _icon.observe(update_icon)  # TO DO - where should this go?
        return ipw.VBox([
            self.tools_dropdown,
            modify_section,
            self.error,
            ipw.HBox([ipw.HTML(value="", layout=ipw.Layout(width='135px')), self.modify_button, self.install_button]),
            ipw.HBox([ipw.HTML(value="", layout=ipw.Layout(width='135px')), self.clear_button, self.uninstall_button]),
            self.snackbar
        ])

    def update_tool_dropdown(self):
        self.tools_dropdown.options = self.available_tools
     
    @property
    def available_tools(self):
        search_results = spy.addons.search(query = {"Name":"*"}, quiet=True)
        return [] if search_results.empty else search_results[['ID', 'Name']].set_index('Name').to_dict()['ID']
    
    @property
    def selected_tool(self):
        return spy.addons.search(query = {"ID": self.tools_dropdown.value}, quiet=True)
    
    def modify_tool(self, _):
        self.modify_button.description = 'modifying...'
        self.modify_button.disabled = True
        current_tool = widget_to_dict()
        current_tool['ID'] = self.tools_dropdown.value
        current_tool.setdefault('Groups', [])
        
        
        if 'Users' not in current_tool.keys():
            current_tool['Users'] = []
        else:
            current_tool['Users'] = list(itertools.chain.from_iterable([self.get_username_from_email(x) for x in current_tool['Users']]))

        if not self.snackbar.v_model:
            try:
                spy.addons.install(tool = current_tool, update_permissions=True, update_tool=True, quiet=True)
                self.snackbar.children = [f'"{current_tool["Name"]}" updated successfully']
                self.snackbar.color = 'success'
                self.update_tool_dropdown()
                self.snackbar.v_model = True
                
            except Exception as e:
                self.snackbar.children = [str(e)]
                self.snackbar.color = 'error'
                self.snackbar.v_model = True
        self.modify_button.description = 'Modify'
        self.modify_button.disabled = False   
    
    
    def install_tool(self, _):
        self.install_button.description = 'installing...'
        self.install_button.disabled = True
        current_tool = widget_to_dict()
    
        
        if 'Users' not in current_tool.keys():
            current_tool['Users'] = []
        else:
            current_tool['Users'] = list(itertools.chain.from_iterable([self.get_username_from_email(x) for x in current_tool['Users']]))      
        
        if self.snackbar.v_model and 'Could not locate user' in str(self.snackbar.children):
            self.snackbar.children = [f'Could not locate user']
            self.snackbar.color = 'error'
            self.snackbar.v_model = True
            return
        
        if not self.available_tools or _name.value not in self.available_tools.keys():
            try:
                spy.addons.install(tool = current_tool, quiet=True)
                self.snackbar.children = [f'"{current_tool["Name"]}"" successfully installed']
                self.snackbar.color = 'success'
                self.update_tool_dropdown()
                self.tools_dropdown.index = list(self.tools_dropdown.options.keys()).index(_name.value)
                self.snackbar.v_model = True
            except Exception as e:
                self.snackbar.children = [str(e)]
                self.snackbar.color = 'error'
                self.snackbar.v_model = True
        else:
            self.snackbar.children = [f'A tool named "{_name.value}" already exists.']
            self.snackbar.color = 'error'
            self.snackbar.v_model = True
        self.install_button.description = 'Install'
        self.install_button.disabled = False
        
    def uninstall_tool(self, _):
        self.uninstall_button.description = 'uninstalling...'
        self.uninstall_button.disabled = True
        spy.addons.uninstall(self.selected_tool, quiet = True)
        self.snackbar.children = [f'"{_name.value}" uninstalled']
        self.snackbar.color = 'success'
        self.snackbar.v_model = True
        self.update_tool_dropdown()
        
        self.uninstall_button.description = 'Uninstall'
        self.uninstall_button.disabled = False

In [22]:
display(vue.ProgressLinear(indeterminate=True, height=10, color='#008a00'))
ui = UserInterface()
clear_output(wait=False)
ui.run()
update_icon(_)